## Example for sharpening UAV thermal imagery.

#### Note: 
This notebook showcase how to use pyDMS using UAV collected thermal and multispectral imagery. Thermal imagery has a coarser resolution than multispectral one. 

NOTE: UAV integrated multispectral and thermal sensors (like Altum and Altum PT) resample data using internal cubic convolution to match the thermal data to multispectral resolution (this has not been tested yet in this code).

#### First install these libraries in the environment (if running the first time)

We will need three images: multispectral, thermal and a mask (in this particular case, filled with the 255 value). The mask is to ensure multispectral and thermal images share a common area. Finally, we need a name for the resulting sharpenned thermal imagery.

Note that the multispectral imagery can also be a DSM, a vegetation index. The idea here is to have as much information about the surface at high resolution that a merged multispectral+DSM imagery is a good idea (not implemented here)

### The configuration of pyDMS is relativey easy:

- algorithm to use: RandomForest (useDecisionTree = True) or Neural Networks (useDecisionTree = False)
- sharpening temperature: yes (disaggregatingTemperature = True) or another data (disaggregatingTemperature = False)
    

In [ ]:
useDecisionTree = True # if False, a neural network sharpener will be used
disaggregatingTemperature = True # if false, it will not apply temperature radiometric transformation.
mask_values = 1 # pixels with this value in the lowResMaskFilename will be processed.

### Running the code...

In [1]:
import os
import time

import pandas as pd

from pathlib import Path
from osgeo import gdal

import pyDMS.pyDMSUtils as utils
from pyDMS.pyDMS import DecisionTreeSharpener, NeuralNetworkSharpener
from pyDMS.pyDMS import REG_sknn_ann, REG_sklearn_ann


In [3]:
# Read input Excel table
excel_table = r"E:\AGU_2025\TSEB_files\input_generation\01_tseb_inputs.xlsx"
# excel_table = r"E:\AGU_2025\TSEB_files\input_generation\01_tseb_inputs_bar.xlsx"
df = pd.read_excel(excel_table, header=0)
num_runs = len(df)
display(df)
print("There are ", num_runs, "runs the model will excecute.")

run_id                                   multiband_raster  \
0  RIP_720  E:\AGU_2025\TSEB_files\input_generation\DATA\R...   
1  RIP_760  E:\AGU_2025\TSEB_files\input_generation\DATA\R...   
2      BAR  E:\AGU_2025\TSEB_files\input_generation\DATA\B...   
3      BAR  E:\AGU_2025\TSEB_files\input_generation\DATA\B...   
4      SLM  E:\AGU_2025\TSEB_files\input_generation\DATA\S...   
5  SLM_001  E:\AGU_2025\TSEB_files\input_generation\DATA\S...   

                                          dsm_raster  \
0  E:\AGU_2025\TSEB_files\input_generation\DATA\R...   
1  E:\AGU_2025\TSEB_files\input_generation\DATA\R...   
2  E:\AGU_2025\TSEB_files\input_generation\DATA\B...   
3  E:\AGU_2025\TSEB_files\input_generation\DATA\B...   
4  E:\AGU_2025\TSEB_files\input_generation\DATA\S...   
5  E:\AGU_2025\TSEB_files\input_generation\DATA\S...   

                                          chm_raster  \
0  E:\AGU_2025\TSEB_files\input_generation\DATA\R...   
1  E:\AGU_2025\TSEB_files\input_generation\DATA\R...   
2  E:\AGU_2025\TSEB_files\input_generation\DATA\B...   
3  E:\AGU_2025\TSEB_files\input_generation\DATA\B...   
4  E:\AGU_2025\TSEB_files\input_generation\DATA\S...   
5  E:\AGU_2025\TSEB_files\input_generation\DATA\S...   

                                          tir_raster  \
0  E:\AGU_2025\TSEB_files\input_generation\DATA\R...   
1  E:\AGU_2025\TSEB_files\input_generation\DATA\R...   
2  E:\AGU_2025\TSEB_files\input_generation\DATA\B...   
3  E:\AGU_2025\TSEB_files\input_generation\DATA\B...   
4  E:\AGU_2025\TSEB_files\input_generation\DATA\S...   
5  E:\AGU_2025\TSEB_files\input_generation\DATA\S...   

                                            mask_shp  fishnet_grid_size  \
0  E:\AGU_2025\TSEB_files\input_generation\DATA\S...                3.4   
1  E:\AGU_2025\TSEB_files\input_generation\DATA\S...                3.0   
2  E:\AGU_2025\TSEB_files\input_generation\DATA\S...                3.4   
3  E:\AGU_2025\TSEB_files\input_generation\DATA\S...                3.6   
4  E:\AGU_2025\TSEB_files\input_generation\DATA\S...                3.6   
5  E:\AGU_2025\TSEB_files\input_generation\DATA\S...                3.4   

   w_c_min  ndvi_threshold  chm_threshold  c_bh_ratio  
0      0.5            0.62            0.5         0.5  
1      0.5            0.62            0.5         0.5  
2      0.5            0.62            0.5         0.5  
3      0.5            0.62            0.5         0.5  
4      0.5            0.62            0.5         0.5  
5      0.5            0.62            0.5         0.5

There are  6 runs the model will excecute.


In [ ]:
# highResFilename = r"inputs\SLM_RGBNIR_vineyards_small.tif" # it can be multispectral, RGB, DSM, vegetation index.
# lowResFilename = r"inputs\SLM_TIR_vineyards_small.tif"
# lowResMaskFilename = r"inputs\SLM_TIR_mask_small.tif" # this can be original TIR * 0 + 1
# outputFilename = r"outputs\TIR_sharpened.tif"

# Base output directory
OUTPUT_BASE = Path(r"E:\AGU_2025\TSEB_files\input_generation\outputs_temp_sharp")
OUTPUT_BASE.mkdir(parents=True, exist_ok=True)
# Start timer
start_time = time.time()
print("Workflow started...")
# Loop to itearate over each row in the df
for i in range(len(df)):
        # print current run
        print(f"Starting run {i+1}/{num_runs} with multiband: {df['run_id'].iloc[i]}")
        highResFilename = Path(df['multiband_raster'].iloc[i])
        lowResFilename = Path(df['tir_raster'].iloc[i])
        # chm_raster = Path(df['chm_raster'].iloc[i])
        
        # Validate paths
        if not highResFilename.exists():
                raise FileNotFoundError(f"Raster not found: {highResFilename}")
        if not lowResFilename.exists():
                raise FileNotFoundError(f"Raster not found: {lowResFilename}")
         # ---------------------------------------------------------------OUTPUTS------------------------------------------------------  
        # Create output folder, named after multiband file (without extension)
        # e.g., from E:\AGU_2025\TSEB_files\input_generation\DATA\RIP\RIP_720_20190504_1025_RGBNIR.tif to RIP_720_20190504_1025
        run_name = "_".join(highResFilename.stem.split("_")[:-1])
        output_dir = OUTPUT_BASE / (run_name)
        output_dir.mkdir(parents=True, exist_ok=True)
        # outputs paths
        outputFilename=os.path.join(output_dir, run_name + "TIR_sharp.tif") # TIR sharpened path
        #----------------------------------------------------------------Workflow------------------------------------------------------
        
        # Create mask in memory without saving to disk
        lowResThermal = gdal.Open(lowResFilename)
        data_LR = lowResThermal.GetRasterBand(1).ReadAsArray().astype(float)
        gt_LR = lowResThermal.GetGeoTransform()
        proj_LR = lowResThermal.GetProjection()

        # Create mask and save to disk (this is needed because the disaggregator needs a file path for the mask)
        mask = data_LR * 0 + 1
        mask_path = output_dir / f"thermal_msk_{i}.tif"
        utils.saveImg(mask, gt_LR, proj_LR, str(mask_path))
        lowResMaskFilename = str(mask_path)


        commonOpts = {"highResFiles":               [highResFilename],
                  "lowResFiles":                [lowResFilename],
                  "lowResQualityFiles":         [lowResMaskFilename], # Using the created mask
                  "lowResGoodQualityFlags":     [mask_values], #this is the value of the mask that indicates good quality pixels
                  "cvHomogeneityThreshold":     0,
                  "movingWindowSize":           15,
                  "disaggregatingTemperature":  [disaggregatingTemperature]}

        dtOpts =     {"perLeafLinearRegression":    True,
                        "linearRegressionExtrapolationRatio": 0.25}

        sknnOpts =   {'hidden_layer_sizes':         (10,),
                        'activation':                 'tanh'}

        nnOpts =     {"regressionType":             REG_sklearn_ann,
                        "regressorOpt":               sknnOpts}

        # start_time = time.time()

        if useDecisionTree:
                opts = commonOpts.copy()
                opts.update(dtOpts)
                disaggregator = DecisionTreeSharpener(**opts)
        else:
                opts = commonOpts.copy()
                opts.update(nnOpts)
                disaggregator = NeuralNetworkSharpener(**opts)

        print("Training regressor...")
        disaggregator.trainSharpener()
        print("Sharpening...")
        downscaledFile = disaggregator.applySharpener(highResFilename, lowResFilename)
        print("Residual analysis...")
        residualImage, correctedImage = disaggregator.residualAnalysis(downscaledFile, lowResFilename,
                                                                        lowResMaskFilename,
                                                                        doCorrection=True)
        print("Saving output...")
        highResFile = gdal.Open(highResFilename)
        if correctedImage is not None:
                outImage = correctedImage
        else:
                outImage = downscaledFile
        # outData = utils.binomialSmoother(outData)
        outFile = utils.saveImg(outImage.GetRasterBand(1).ReadAsArray(),
                                outImage.GetGeoTransform(),
                                outImage.GetProjection(),
                                outputFilename)
        residualFile = utils.saveImg(residualImage.GetRasterBand(1).ReadAsArray(),
                                        residualImage.GetGeoTransform(),
                                        residualImage.GetProjection(),
                                        os.path.splitext(outputFilename)[0] + "_residual" +
                                        os.path.splitext(outputFilename)[1])

        outFile = None
        residualFile = None
        downscaledFile = None
        highResFile = None

print(time.time() - start_time, "seconds")

Workflow started...
Starting run 1/6 with multiband: RIP_720


c:\Users\A02424951\AppData\Local\anaconda3\envs\temp_sharp\Lib\site-packages\osgeo\gdal.py:606: FutureWarning: Neither gdal.UseExceptions() nor gdal.DontUseExceptions() has been explicitly called. In GDAL 4.0, exceptions will be enabled by default.
  warnings.warn(


Saved E:\AGU_2025\TSEB_files\input_generation\outputs_temp_sharp\RIP_720_20190504_1025\thermal_msk_0.tif
Training regressor...
Homogeneity CV threshold: 0.13
Number of training elements for is 130 representing 100% of avaiable low-resolution data.
Homogeneity CV threshold: 0.15
Number of training elements for is 220 representing 100% of avaiable low-resolution data.
Homogeneity CV threshold: 0.17
Number of training elements for is 220 representing 100% of avaiable low-resolution data.
Homogeneity CV threshold: 0.17
Number of training elements for is 220 representing 100% of avaiable low-resolution data.
Homogeneity CV threshold: 0.18
Number of training elements for is 220 representing 100% of avaiable low-resolution data.
Homogeneity CV threshold: 0.18
Number of training elements for is 220 representing 100% of avaiable low-resolution data.
Homogeneity CV threshold: 0.21
Number of training elements for is 220 representing 100% of avaiable low-resolution data.
Homogeneity CV threshold: 